# Mega API 測試 Notebook

## 1. 限制

1. 證券無預約單功能，請在各盤別交易時間下單
2. 不支援興櫃交易
3. 如在其他平台的委託(如兆豐贏家、理財通等...)，API會收不到主動回報及成交回報，但可以用API的委託查詢、成交查詢查到委託狀態，並可刪改單
4. API委託的錯誤單在其他平台查不到
5. 每秒委託限制20筆，超過的委託會被拒絕

## 2. 測試環境下單

1. 證券下單時間: 09:40~21:00
2. 開通正式環境使用權限以前，開通證券的客戶至少需完成測試環境「整股」委託刪單、減量、改價、成交測試(可下市價單與市場的其他人成交或者自己下買單和賣單成交)

## 3. 範例需修改地方

第一個程式區塊，修改個人資料



## 4. 正式環境連線
當測試報告書完成後且收到公司通知已開通，如要下單到正式環境需修改以下兩個連線

1. speedyAPI_config.json裡的spapitest 改為 spapi
2. ObjOrder.Connect 裡的 spapitest 改為 spapi





## 5. Notebook 說明
本 Notebook 將證券、期貨及選擇權的委託、刪單、改單（改價或減量）測試流程拆分為多個 Cell。
每個 Cell 都會使用預先定義好的參數進行測試，並利用 logging 輸出回報訊息，
方便確認委託與成交回報是否正確。

**注意：**
1. 委託成功後，回報中的 `OrderID` 與 `SendNewOrderEx` 回傳的 `nid` 不同；
   刪單及改單時必須使用回調中的 `OrderID`。
2. 各市場的參數有所不同，例如證券下單的 TWSEOrdTyp 為 "0"；
   期貨及選擇權下單中部分參數需留空（例如期貨的 TWSEOrdTyp 為空字串）。

## 6. 其他知識點
- **Python 模組與 package：**
  本程式碼使用了 Mega API 的 Python package（例如 `megaSpeedy.spdOrderAPI`），
  並假設你已依照官方說明將相應 package 放置到 Python 的環境中（或虛擬環境內的 site-packages 目錄）。
- **logging 模組：**
  用於記錄訊息與除錯資訊，設定了輸出格式與等級，方便觀察程式執行狀態。
- **回傳結果處理：**
  API 回傳的結果通常為 JSON 格式，利用 `json.dumps` 可以格式化輸出，
  而使用 Pandas 將 list 轉 DataFrame 可方便檢視資料表格形式的內容。


In [19]:
import time
import os
import logging

# 設定 logging 格式與等級
logging.basicConfig(level=logging.INFO, format='%(asctime)s %(levelname)s: %(message)s')
logging.info('初始化環境完成')


# 請將以下變數值，改為自己的資料
UID='A123456789' #身分證字號字母大寫
LoginPW='1234' #登入密碼
SKBranchid='7000' #分公司別 7000為總公司
SKAcc='1234567' #證券帳號
CAPath='1234.pfx' #憑證路徑
CAPW='A123456789' #憑證密碼，測試環境預設同身分證字號



2025-04-22 10:56:47,160 INFO: 初始化環境完成


In [20]:
from megaSpeedy.spdOrderAPI import spdOrderAPI
import uuid
class testPyOrderAPI(spdOrderAPI):
    """
    Speedy API 測試類別
    此類別繼承自官方提供的 spdOrderAPI，並覆寫了部分回調函式
    以便在委託下單、刪單、改單及成交回報時，能夠記錄詳細資訊。
    """
    def __init__(self):
        # 呼叫父類別建構子以初始化底層 API 連結
        super().__init__()
        self.FIsLogon = False
        self.lastOrderID = None  # 用來儲存最新委託回報中的 OrderID，供取消或改單使用
        

    def OnConnected(self):
        logging.info('-------------- OnConnected() --------------')
        # 使用憑證內的帳號 (此處範例使用 "A123456789")
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '證券帳號七位數如:[0023456]')
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '期貨帳號七位數如:[0023456]')
        # 登入證期市場逗號分隔
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '證券帳號七位數如:[0023456],期貨帳號七位數如:[0023456]')
        if not self.LogonProxy(UID, LoginPW, SKAcc ):
            logging.error(f'登入失敗! {self.GetLastErrorMsg()}')
            raise Exception("條件不符，中斷執行！")



    def OnDisconnected(self):
        logging.info('-------------- OnDisconnected() --------------')
        self.FIsLogon = False

    def OnLogonResponse(self, IsSucceed, ReplyString):
        logging.info('-------------- OnLogonResponse() --------------')
        logging.info(f'--- IsSucceed: {IsSucceed} ReplyString: {ReplyString}')
        if IsSucceed:
            self.FIsLogon = True
            # 設定各市場下單帳號
            # self.SetAccount( '市場', '分公司別', '帳號')
            self.SetAccount('TAIFEX', 'F030000', '0023456')  # 期貨帳號 公司別固定為F030000
            self.SetAccount('TWSE', SKBranchid, SKAcc )        # 證券帳號 公司別依照下單帳號的公司別
            self.SetAccount('US', '7000', '023456')           # 複委託帳號
        else:
            logging.error(f"登入失敗. {ReplyString}")

    def OnReplyNewOrder(self, NID, UDD, Symbol, Price, Side, OrderQty, OrderType, TimeInForce, OrderID):
        logging.info('-------------- OnReplyNewOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side}')
        logging.info(f'--- OrderQty: {OrderQty} OrderType: {OrderType} TimeInForce: {TimeInForce} OrderID: {OrderID}')
        # 儲存回報中的 OrderID 以便後續取消或改單時使用
        self.lastOrderID = OrderID

    def OnReplyCancelOrder(self, NID, UDD, Symbol, Price, Side, OrderID):
        logging.info('-------------- OnReplyCancelOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side} OrderID: {OrderID}')

    def OnReplyReplaceOrder(self, NID, UDD, Symbol, Price, Side, OrderQty, OrderType, TimeInForce, OrderID):
        logging.info('-------------- OnReplyReplaceOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side}')
        logging.info(f'--- OrderQty: {OrderQty} OrderType: {OrderType} TimeInForce: {TimeInForce} OrderID: {OrderID}')

    def OnRejectOrder(self, NID, UDD, ActionFrom, ErrCode, ErrMsg):
        logging.info('-------------- OnRejectOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} ActionFrom: {ActionFrom} ErrCode: {ErrCode} ErrMsg: {ErrMsg}')

    def OnFill(self, NID, UDD, OrderID, ReportSequence, FillPrice, FillQty, FillTime):
        logging.info('-------------- OnFill() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} OrderID: {OrderID} ReportSequence: {ReportSequence}')
        logging.info(f'--- FillPrice: {FillPrice} FillQty: {FillQty} FillTime: {FillTime}')


def json_to_dataframe(json_data):
    """
    將 JSON 字串或字典轉換為 Pandas DataFrame
    
    :param json_data: JSON 字串或字典
    :return: Pandas DataFrame（成功）或 None（失敗）
    """
    # 如果是字串，嘗試解析為字典
    if isinstance(json_data, str):
        try:
            json_data = json.loads(json_data)  # 解析 JSON
        except json.JSONDecodeError:
            print("❌ 解析 JSON 失敗，請檢查資料格式")
            return None

    # 檢查 JSON 結構是否符合預期
    if not isinstance(json_data, dict) or "Data" not in json_data or "Title" not in json_data:
        print("❌ 錯誤：JSON 不是預期的格式")
        return None

    if not isinstance(json_data["Data"], list) or not isinstance(json_data["Title"], list):
        print("❌ 錯誤：JSON 中的 'Data' 或 'Title' 不是 list")
        return None

    # 建立 DataFrame
    try:
        df = pd.DataFrame(json_data["Data"], columns=json_data["Title"])
        return df
    except Exception as e:
        print(f"❌ 建立 DataFrame 失敗: {e}")
        return None

from IPython.display import HTML, display
import pandas as pd

def display_fixed_scroll_top(df, freeze_cols=1, height='400px'):
    html = df.to_html(classes='my-table', border=1)

    style = f"""
    <style>
    .outer-container {{
        position: relative;
        overflow: hidden;
        max-width: 100%;
    }}
    .scroll-container {{
        overflow: auto;
        height: {height};
        width: 100%;
    }}
    .my-table {{
        border-collapse: collapse;
        width: max-content;
        min-width: 100%;
    }}
    .my-table th, .my-table td {{
        padding: 8px 12px;
        border: 1px solid #ccc;
        white-space: nowrap;
    }}
    .my-table thead th {{
        position: sticky;
        top: 0;
        background: #f5f5f5;
        z-index: 2;
    }}
    /* Freeze left columns */
    .my-table td:nth-child(-n+{freeze_cols}),
    .my-table th:nth-child(-n+{freeze_cols}) {{
        position: sticky;
        left: 0;
        background: #f5f5f5;
        z-index: 1;
    }}
    .my-table thead th:nth-child(-n+{freeze_cols}) {{
        z-index: 3;
    }}
    </style>
    """

    # Outer container lets the top scroll bar appear above
    html_wrapped = f'''
    <div class="outer-container">
        <div class="scroll-container">
            {html}
        </div>
    </div>
    '''
    display(HTML(style + html_wrapped))


In [21]:
# 實例化 API 物件，並設定憑證
# 請確保 A123456789.pfx 憑證檔案放置於工作目錄下
#ObjOrder.EnableMEGACA("憑證檔路徑","身分證字號(大寫字母)","憑證密碼")
ObjOrder = testPyOrderAPI()
result = ObjOrder.EnableMEGACA(CAPath, UID, CAPW)
if result:
    logging.info('已成功設定簽章憑證')
    logging.info('連線中...')
else:
    logging.error(f'簽章憑證設定失敗! {ObjOrder.GetLastErrorMsg()}')
    raise Exception("條件不符，中斷執行！")


ObjOrder.Connect('spapitest.emega.com.tw', 56789, 5)



#以下為自動重連範例，請先確認個人資料都正確才使用，不然帳號會因為錯誤次數太多而被鎖定
"""
Count = 0
while True:
    time.sleep(1)
    if Count % 10 == 0:
        if not ObjOrder.IsConnected():
            ObjOrder.Connect('spapitest.emega.com.tw', 56789, 5)
    Count += 1
    if ObjOrder.FIsLogon:
        logging.info('登入成功！')
        break
logging.info('連線及登入程序完成')
"""

2025-04-22 10:56:49,104 ERROR: 簽章憑證設定失敗! 簽章測試失敗,密碼錯誤


Exception: 條件不符，中斷執行！

## 證券測試流程 (請依序執行下面各個 Cell)

In [35]:
# 證券新單委託測試
securities_order = {
    "Market": "tse",         # 證券市場
    "Symbol": "2886",        # 股票代號 2886
    "Price": 37,             # 委託價格 (示例價格)
    "Qty": 1,                  # 委託口數
    "Side": "B",             # 買進委託 ("B" 為買，"S" 為賣)
    "OrderType": "L",        # 限價單
    "Tif": "R",              # 當日有效 (ROD)
    "TS": "N",               # Normal
    "PE": "A",               # PositionEffect (預設 A)
    "TO": "0"                # 證券一般委託 TWSEOrdTyp 為 "0"
}

securities_new_nid = ObjOrder.SendNewOrderEx(
    securities_order["Market"],
    "testUDD_New",
    securities_order["Symbol"],
    securities_order["Price"],
    securities_order["Side"],
    securities_order["Qty"],
    securities_order["OrderType"],
    securities_order["Tif"],
    securities_order["TS"],
    securities_order["PE"],
    securities_order["TO"]
)

if securities_new_nid == 0:
    logging.error(f"證券新單委託失敗: {ObjOrder.GetLastErrorMsg()}")
else:
    logging.info(f"證券新單委託成功, nid={securities_new_nid}")
    logging.info(f"取得的 OrderID 為: {ObjOrder.lastOrderID}")


2025-04-14 13:10:37,348 INFO: 證券新單委託成功, nid=49265
2025-04-14 13:10:37,349 INFO: 取得的 OrderID 為: x0004
2025-04-14 13:10:37,362 INFO: -------------- OnReplyNewOrder() --------------
2025-04-14 13:10:37,364 INFO: --- NID: 49265 UDD:                      Symbol: 2886 Price: 37.0 Side: B
2025-04-14 13:10:37,365 INFO: --- OrderQty: 1 OrderType: L TimeInForce: R OrderID: x0005


In [30]:
# 證券刪單委託測試
# 使用從新單回調中取得的 OrderID
if ObjOrder.lastOrderID is None:
    logging.error('未取得證券新單回報的 OrderID，無法執行刪單測試')
else:
    cancel_order_sec = {
        "Market": securities_order["Market"],
        "Symbol": securities_order["Symbol"],
        "Price": securities_order["Price"],
        "Side": securities_order["Side"],  # 與下單時相同
        "OrderID": ObjOrder.lastOrderID,     # 使用回報中的訂單編號
        "TS": securities_order["TS"],
        "TO": securities_order["TO"]
    }
    
    securities_cancel_nid = ObjOrder.SendCancelOrderEx(
        cancel_order_sec["Market"],
        "testUDD_Cancel",
        cancel_order_sec["Symbol"],
        cancel_order_sec["Price"],
        cancel_order_sec["Side"],
        cancel_order_sec["OrderID"],
        cancel_order_sec["TS"],
        cancel_order_sec["TO"]
    )
    
    if securities_cancel_nid == 0:
        logging.error(f"證券刪單委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"證券刪單委託成功, nid={securities_cancel_nid}")


2025-04-14 12:26:58,832 INFO: 證券刪單委託成功, nid=32882


In [36]:
# 證券改單委託測試 - 改價測試
if ObjOrder.lastOrderID is None:
    logging.error('未取得證券新單回報的 OrderID，無法執行改單測試')
else:
    # 改價：將價格增加 0.5 (例如從 37 改為 37.5)
    replace_order_sec = {
        "Market": securities_order["Market"],
        "Symbol": securities_order["Symbol"],
        "Price": securities_order["Price"] + 0.5,
        "Qty": 0,
        "Side": securities_order["Side"],
        "OrderID": ObjOrder.lastOrderID,
        "OrderType": securities_order["OrderType"],
        "Tif": securities_order["Tif"],
        "TS": securities_order["TS"],
        "TO": securities_order["TO"]
    }
    
    securities_replace_nid = ObjOrder.SendReplaceOrderEx(
        replace_order_sec["Market"],
        "testUDD_Replace",
        replace_order_sec["Symbol"],
        replace_order_sec["OrderID"],
        replace_order_sec["Side"],
        replace_order_sec["Price"],
        replace_order_sec["Qty"],
        replace_order_sec["OrderType"],
        replace_order_sec["Tif"],
        replace_order_sec["TS"],
        replace_order_sec["TO"]
    )
    
    if securities_replace_nid == 0:
        logging.error(f"證券改單委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"證券改單委託成功, nid={securities_replace_nid}")


2025-04-14 13:10:47,689 INFO: 證券改單委託成功, nid=16499
2025-04-14 13:10:47,702 INFO: -------------- OnReplyReplaceOrder() --------------
2025-04-14 13:10:47,705 INFO: --- NID: 16499 UDD:                      Symbol: 2886 Price: 37.5 Side: B
2025-04-14 13:10:47,706 INFO: --- OrderQty: 0 OrderType: L TimeInForce: R OrderID: x0005


In [37]:
# 證券改單委託測試 - 減量測試
if ObjOrder.lastOrderID is None:
    logging.error('未取得證券新單回報的 OrderID，無法執行改單測試')
else:
    # 減量輸入1
    replace_order_sec = {
        "Market": securities_order["Market"],
        "Symbol": securities_order["Symbol"],
        "Price": securities_order["Price"],
        "Qty": 1,
        "Side": securities_order["Side"],
        "OrderID": ObjOrder.lastOrderID,
        "OrderType": securities_order["OrderType"],
        "Tif": securities_order["Tif"],
        "TS": securities_order["TS"],
        "TO": securities_order["TO"]
    }
    
    securities_replace_nid = ObjOrder.SendReplaceOrderEx(
        replace_order_sec["Market"],
        "testUDD_Replace",
        replace_order_sec["Symbol"],
        replace_order_sec["OrderID"],
        replace_order_sec["Side"],
        replace_order_sec["Price"],
        replace_order_sec["Qty"],
        replace_order_sec["OrderType"],
        replace_order_sec["Tif"],
        replace_order_sec["TS"],
        replace_order_sec["TO"]
    )
    
    if securities_replace_nid == 0:
        logging.error(f"證券改單委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"證券改單委託成功, nid={securities_replace_nid}")


2025-04-14 13:10:55,488 INFO: 證券改單委託成功, nid=32883
2025-04-14 13:10:55,501 INFO: -------------- OnReplyReplaceOrder() --------------
2025-04-14 13:10:55,503 INFO: --- NID: 32883 UDD:                      Symbol: 2886 Price: 0.0 Side: B
2025-04-14 13:10:55,504 INFO: --- OrderQty: 0 OrderType: L TimeInForce: R OrderID: x0005


In [42]:
import json
import pandas as pd

# 證券委託查詢測試
# 建立查詢參數，所有參數皆以字串表示
query_param = {
    "branch_id": SKBranchid,       # 分公司代碼 (必填)，證券市場總公司代碼為 7000
    "cust_id": SKAcc,       # 客戶帳號 (必填)，請依實際情況設定
    "stock_no": "",         # 股票代號 (可選)，可輸入股票代號或空字串
    "apcode": "0",             # 盤別 (必填)： '0':全部, '1':整股, '2':盤後, '3':零股, '4':興櫃, '5':盤中零股
    "market": "0",             # 市場別 (必填)： '0':全部, '1':集中, '2':櫃台, '3':興櫃
    "qry_type": "0"            # 委託別 (必填)： '0':全部, '1':預約, '2':盤中, '3':可取消, '4':失敗的委託
}

# 呼叫 queryStkOrder 進行證券委託查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryStkOrder(query_param)


# 使用 json.dumps 格式化輸出查詢結果
pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("證券委託查詢結果:")
print(pretty_result)

api_result = json.loads(api_result)

# 若 api_result 中有委託資料 (ackList)，將其轉為 DataFrame 表格顯示，方便閱讀
if "ackList" in api_result and api_result["ackList"]:
    df = pd.DataFrame(api_result["ackList"])
    display(df)
else:
    logging.info("查詢結果中無委託資料")


證券委託查詢結果:
"{\"result\":\"0\",\"ackList\":[{\"errcode\":\"00000000\",\"orddate\":\"20250414\",\"apcode\":\"1\",\"avg_price\":\"0\",\"chgdate\":\"20250414\",\"mattime\":\"\",\"requestno\":\"\",\"odprice\":\"37.5\",\"chgtime\":\"131053000\",\"syscode\":\"PI\",\"bs_flag\":\"R\",\"act\":\"M\",\"matqty\":\"0\",\"celqty\":\"1\",\"workdate\":\"20250414\",\"celable\":\"2\",\"priceflag\":\"0\",\"errmsg\":\"\",\"preordno\":\"\",\"market\":\"T\",\"buysell\":\"B\",\"orgqty\":\"1\",\"ordno\":\"x0005\",\"trade\":\"0\",\"ordstatus\":\"2\",\"ordtime\":\"131046000\",\"stockno\":\"2886\"},{\"errcode\":\"00000000\",\"orddate\":\"20250414\",\"apcode\":\"1\",\"avg_price\":\"27.0\",\"chgdate\":\"20250414\",\"mattime\":\"130317000\",\"requestno\":\"1130300639800004\",\"odprice\":\"27.0\",\"chgtime\":\"130311000\",\"syscode\":\"SI\",\"bs_flag\":\"R\",\"act\":\"O\",\"matqty\":\"1\",\"celqty\":\"0\",\"workdate\":\"20250414\",\"celable\":\"2\",\"priceflag\":\"2\",\"errmsg\":\"\",\"preordno\":\"\",\"market\":\"T\"

errcode   orddate apcode avg_price   chgdate    mattime         requestno  \
0  00000000  20250414      1         0  20250414                                
1  00000000  20250414      1      27.0  20250414  130317000  1130300639800004   
2  00000000  20250414      1      27.0  20250414  130317000  1130300639800003   
3  00000000  20250414      1         0  20250414             1130300639800002   
4  00000000  20250414      1      27.0  20250414  130307000  1130300639800001   
5  00000000  20250414      1         0  20250414                                
6  00000000  20250414      1         0  20250414                                
7  00000000  20250414      1      37.0  20250414  112256000                     
8      1030  20250414      1         0  20250414                                
9      8895  20250414      1         0  20250414                                

  odprice    chgtime syscode  ...           errmsg preordno market buysell  \
0    37.5  131053000      PI  ...                                T       B   
1    27.0  130311000      SI  ...                                T       B   
2    27.0  130307000      SI  ...                                T       B   
3    27.0  130303000      SI  ...                                T       B   
4    27.0  130300000      SI  ...                                T       B   
5    37.0  112406000      PI  ...                                T       B   
6    37.0  112345000      PI  ...                                T       B   
7    37.0  112249000      PI  ...                                T       B   
8     1.0  093507021      PI  ...      委託價超出今日漲跌幅。               T       B   
9     1.0  083009881      DL  ...  檢核程式不存在[Speedy]               T       B   

  orgqty  ordno trade ordstatus    ordtime stockno  
0      1  x0005     0         2  131046000    2886  
1      1  z001h     0         2  130311000    1101  
2      1  z001g     0         2  130307000    1101  
3      1  z001f     0         2  130303000    1101  
4      1  z001d     0         2  130300000    1101  
5      1  x0004     0         2  112401000    2886  
6      1  x0003     0         2  112341000    2886  
7      1  x0002     0         2  112249000    2886  
8      1  x0001     0         2  093507021    2886  
9      1            0         2  083009881    2886  

[10 rows x 27 columns]

In [43]:
import json
import pandas as pd  # 請先安裝 pandas 套件 (pip install pandas)

# 證券成交查詢測試
# 建立查詢參數 (所有參數皆以字串表示)
query_param = {
    "branch_id": SKBranchid,      # 分公司代碼 (必填)
    "cust_id": SKAcc,      # 客戶帳號 (必填)
    "stock_no": "",        # 股票代號 (可選)，此處查詢 2886，或空字串
    "qry_type": "0"            # 委託別 (必填)： '0' 表示成交明細，'1' 表示成交彙總
}

# 呼叫 queryStkMatch 進行證券成交查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryStkMatch(query_param)

# 使用 json.dumps 格式化輸出查詢結果
pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("證券成交查詢結果:")
print(pretty_result)

api_result = json.loads(api_result)

# 若 api_result 中有成交明細 (ordList)，將其轉成 DataFrame 表格顯示
if "ordList" in api_result and api_result["ordList"]:
    df = pd.DataFrame(api_result["ordList"])
    display(df)
else:
    logging.info("查詢結果中無成交資料")


證券成交查詢結果:
"{\"result\":\"0\",\"message\":\"執行成功\",\"ordList\":[{\"match_qty\":\"1000\",\"pay_price\":\"27000\",\"stock_no\":\"1101\",\"apcode\":\"1\",\"match_time\":\"130317000\",\"source\":\"SI\",\"market\":\"T\",\"buysell\":\"B\",\"mkt_seq_num\":\"00000074\",\"ordno\":\"z001h\",\"trade\":\"0\",\"mat_date\":\"20250414\",\"price\":\"27.0\"},{\"match_qty\":\"1000\",\"pay_price\":\"27000\",\"stock_no\":\"1101\",\"apcode\":\"1\",\"match_time\":\"130317000\",\"source\":\"SI\",\"market\":\"T\",\"buysell\":\"B\",\"mkt_seq_num\":\"00000073\",\"ordno\":\"z001g\",\"trade\":\"0\",\"mat_date\":\"20250414\",\"price\":\"27.0\"},{\"match_qty\":\"1000\",\"pay_price\":\"27000\",\"stock_no\":\"1101\",\"apcode\":\"1\",\"match_time\":\"130307000\",\"source\":\"SI\",\"market\":\"T\",\"buysell\":\"B\",\"mkt_seq_num\":\"00000071\",\"ordno\":\"z001d\",\"trade\":\"0\",\"mat_date\":\"20250414\",\"price\":\"27.0\"},{\"match_qty\":\"1000\",\"pay_price\":\"37000\",\"stock_no\":\"2886\",\"apcode\":\"1\",\"match_ti

match_qty pay_price stock_no apcode match_time source market buysell  \
0      1000     27000     1101      1  130317000     SI      T       B   
1      1000     27000     1101      1  130317000     SI      T       B   
2      1000     27000     1101      1  130307000     SI      T       B   
3      1000     37000     2886      1  112256000     PI      T       B   

  mkt_seq_num  ordno trade  mat_date price  
0    00000074  z001h     0  20250414  27.0  
1    00000073  z001g     0  20250414  27.0  
2    00000071  z001d     0  20250414  27.0  
3    00000067  x0002     0  20250414  37.0

In [45]:
import json
import pandas as pd

# 證券帳務查詢測試
# 建立查詢參數 (所有參數皆以字串表示)
query_param = {
    "branch_id": SKBranchid,         # 分公司代碼 (必填)，證券市場總公司代碼為 7000
    "cust_id": SKAcc,         # 客戶帳號 (必填)
    "stkno": "",             # 股票代號 (可選)
    "nocsint": "N",              # 計算除息 (例："Y" 表示不計算)

}

# 呼叫 makeStockAccountInquriy 進行證券帳務查詢，回傳結果為 JSON 格式
api_result = ObjOrder.makeStockAccountInquriy(query_param)

# 使用 json.dumps 格式化輸出查詢結果
pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("證券帳務查詢結果:")
print(pretty_result)

api_result = json.loads(api_result)

# 如果 api_result 中包含 stksumList 或 stktotList，將其轉成 DataFrame 表格顯示
if "stksumList" in api_result and api_result["stksumList"]:
    df = pd.DataFrame(api_result["stksumList"])
    display(df)
elif "stktotList" in api_result and api_result["stktotList"]:
    df = pd.DataFrame(api_result["stktotList"])
    display(df)
else:
    logging.info("查詢結果中無帳務資料")


證券帳務查詢結果:
"{\"result\":\"0\",\"stksumList\":[{\"apcode\":\"\",\"qtyl\":\"1200\",\"settype\":\"0\",\"t32unit\":\"1000\",\"recvasum\":\"39067\",\"qtys\":\"0\",\"makeasum\":\"-2260\",\"stkna\":\"元大高股息\",\"taxgrate\":\"0.00000000\",\"qtyc\":\"0\",\"pricerange\":\"-6.10%\",\"qtyb\":\"0\",\"sflag\":\"X\",\"stkno\":\"0056\",\"taxrate\":\"0.00100000\",\"costsum\":\"-41327\",\"stype\":\"H\",\"markw\":\"0\",\"bhno\":\"7000\",\"priceevn\":\"34.52\",\"qtyfs\":\"0\",\"qtybm\":\"0\",\"priceavg\":\"34.75\",\"cseq\":\"1234567\",\"priceqtysum\":\"41698\",\"stkdatList\":[],\"trade\":\"0\",\"costqty\":\"1200\",\"pricemkt\":\"32.63\",\"pricenow\":\"32.63\",\"valuemkt\":\"39156\",\"valuenow\":\"39156\",\"makeaper\":\"-5.47\",\"qtysm\":\"0\",\"feerate\":\"0.00142500\"},{\"apcode\":\"\",\"qtyl\":\"2600\",\"settype\":\"0\",\"t32unit\":\"1000\",\"recvasum\":\"128473\",\"qtys\":\"0\",\"makeasum\":\"-5190\",\"stkna\":\"元大台灣高息低波\",\"taxgrate\":\"0.00000000\",\"qtyc\":\"0\",\"pricerange\":\"-4.22%\",\"qtyb\":\"0\"

apcode  qtyl settype t32unit recvasum qtys makeasum       stkna    taxgrate  \
0         1200       0    1000    39067    0    -2260       元大高股息  0.00000000   
1         2600       0    1000   128473    0    -5190    元大台灣高息低波  0.00000000   
2         2000       0    1000    39689    0    -2619     國泰永續高股息  0.00000000   
3         2400       0    1000    44420    0    -4935  群益台ESG低碳50  0.00000000   
4         5000       0    1000    65242    0    67817    統一台灣高息動能  0.00000000   
5         5000       0    1000    41999    0    43999    元大台灣價值高息  0.00000000   
6         7500       0    1000    73005    0    -3350    群益優選非投等債  0.00000000   
7            0       0    1000    88842    0     7728          台泥  0.00000000   
8            0       0    1000    37790    0      738         兆豐金  0.00000000   

  qtyc  ... stkdatList trade costqty pricemkt pricenow valuemkt valuenow  \
0    0  ...         []     0    1200    32.63    32.63    39156    39156   
1    0  ...         []     0    2600    49.53    49.53   128778   128778   
2    0  ...         []     0    2000    19.89    19.89    39780    39780   
3    0  ...         []     0    2400    18.55    18.55    44520    44520   
4    0  ...         []     0    5000    13.08    13.08    65400    65400   
5    0  ...         []     0    5000     8.42     8.42    42100    42100   
6    0  ...         []     0    7500     9.75     9.75    73125    73125   
7    0  ...         []     0    3000    29.70    29.70    89100    89100   
8    0  ...         []     0    1000    37.90    37.90    37900    37900   

  makeaper qtysm     feerate  
0    -5.47     0  0.00142500  
1    -3.88     0  0.00142500  
2    -6.19     0  0.00142500  
3   -10.00     0  0.00142500  
4     0.00     0  0.00142500  
5     0.00     0  0.00142500  
6    -4.39     0  0.00142500  
7     9.53     0  0.00142500  
8     1.99     0  0.00142500  

[9 rows x 35 columns]

# 盤後資訊

In [18]:
import json
import pandas as pd
from IPython.display import display, HTML
# GetMKChartData 開高低收成交量/月K線資料
# 設定顯示所有行和列
pd.set_option('display.max_rows', None)   # 顯示所有行
pd.set_option('display.max_columns', None)  # 顯示所有列
pd.set_option('display.width', None)     # 不限制寬度
pd.set_option('display.max_colwidth', None)  # 顯示所有欄位內容（避免截斷）

api_result = ObjOrder.GetMKChartData("2330")
# 使用 json.dumps 格式化輸出查詢結果
#pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("查詢結果:")
#print(pretty_result)
df=json_to_dataframe(api_result)
display_fixed_scroll_top(df, freeze_cols=2)

查詢結果:


In [13]:
import json
import pandas as pd
from IPython.display import display, HTML
# GetMKChartData 開高低收成交量/周K線資料
# 設定顯示所有行和列
pd.set_option('display.max_rows', None)   # 顯示所有行
pd.set_option('display.max_columns', None)  # 顯示所有列
pd.set_option('display.width', None)     # 不限制寬度
pd.set_option('display.max_colwidth', None)  # 顯示所有欄位內容（避免截斷）

api_result = ObjOrder.GetWKChartData("2330")
# 使用 json.dumps 格式化輸出查詢結果
#pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("查詢結果:")
#print(pretty_result)
df=json_to_dataframe(api_result)
display_fixed_scroll_top(df, freeze_cols=2)

查詢結果:


In [14]:
import json
import pandas as pd
from IPython.display import display, HTML
# GetMKChartData 日K/技術指標/價量資料-個股多期
# 設定顯示所有行和列
pd.set_option('display.max_rows', None)   # 顯示所有行
pd.set_option('display.max_columns', None)  # 顯示所有列
pd.set_option('display.width', None)     # 不限制寬度
pd.set_option('display.max_colwidth', None)  # 顯示所有欄位內容（避免截斷）

api_result = ObjOrder.GetDKChartData("2330")
# 使用 json.dumps 格式化輸出查詢結果
#pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("查詢結果:")
#print(pretty_result)
df=json_to_dataframe(api_result)
display_fixed_scroll_top(df, freeze_cols=2)

查詢結果:


In [60]:
import json
import pandas as pd
from IPython.display import display, HTML
# GetMKChartData 還原月K(個股、ETF、大盤)-單股單期
# 設定顯示所有行和列
pd.set_option('display.max_rows', None)   # 顯示所有行
pd.set_option('display.max_columns', None)  # 顯示所有列
pd.set_option('display.width', None)     # 不限制寬度
pd.set_option('display.max_colwidth', None)  # 顯示所有欄位內容（避免截斷）

api_result = ObjOrder.GetAdjustedMKChartData("2330")
# 使用 json.dumps 格式化輸出查詢結果
#pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("查詢結果:")
#print(pretty_result)
df=json_to_dataframe(api_result)
display_fixed_scroll_top(df, freeze_cols=2)

查詢結果:


In [61]:
import json
import pandas as pd
from IPython.display import display, HTML
# GetMKChartData 還原周K(個股、ETF、大盤)-單股單期
# 設定顯示所有行和列
pd.set_option('display.max_rows', None)   # 顯示所有行
pd.set_option('display.max_columns', None)  # 顯示所有列
pd.set_option('display.width', None)     # 不限制寬度
pd.set_option('display.max_colwidth', None)  # 顯示所有欄位內容（避免截斷）

api_result = ObjOrder.GetAdjustedWKChartData("2330")
# 使用 json.dumps 格式化輸出查詢結果
#pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("查詢結果:")
#print(pretty_result)
df=json_to_dataframe(api_result)
display_fixed_scroll_top(df, freeze_cols=2)

查詢結果:


In [62]:
import json
import pandas as pd
from IPython.display import display, HTML
# GetMKChartData 還原日K(個股、ETF、大盤)-單股單期
# 設定顯示所有行和列
pd.set_option('display.max_rows', None)   # 顯示所有行
pd.set_option('display.max_columns', None)  # 顯示所有列
pd.set_option('display.width', None)     # 不限制寬度
pd.set_option('display.max_colwidth', None)  # 顯示所有欄位內容（避免截斷）

api_result = ObjOrder.GetAdjustedDKChartData("2330")
# 使用 json.dumps 格式化輸出查詢結果
#pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("查詢結果:")
#print(pretty_result)
df=json_to_dataframe(api_result)
display_fixed_scroll_top(df, freeze_cols=2)

查詢結果:


# 中斷連線

從jupyter釋放資源

In [40]:
# 測試完畢後斷線並結束程序
ObjOrder.Disconnect()
logging.info('~~~ Program terminate ~~~')

2025-04-17 13:51:41,972 INFO: -------------- OnDisconnected() --------------
2025-04-17 13:51:41,973 INFO: ~~~ Program terminate ~~~


# 即時行情測試

`請修改行情主機IP:QuoteIP`

In [58]:
from megaSpeedy.spdQuoteAPI import spdQuoteAPI
import time, os

QuoteIP='0.0.0.0'

#----------------------------------------------------------------------------
# spdQuoteAPI implementation
#----------------------------------------------------------------------------
class testPyQuoteAPI(spdQuoteAPI):
    def OnConnected(self):
        # implement OnConnected() ...
        print('-------------- OnConnected() --------------')
    def OnDisconnected(self):
        #implement OnDisconnected() ...
        print('-------------- OnDisConnected() --------------')
        pass
    def OnLogonResponse(self, IsSucceed, ReplyString):
        #implement OnLogonResponse() ...
        print('-------------- OnLogonResponse() --------------')
        print('--- IsSucceed:{0} ReplyString:{1}'.format(IsSucceed, ReplyString))                
        global logonOK
        logonOK = IsSucceed        
        pass
    def OnContractDownloadComplete(self):        
        print('-------------- OnContractDownloadComplete() --------------')
        if "2330" in self.Stocks:
            Contract = self.Stocks['2330']
            self.SubscribeContract( Contract )
            Contract.Print()
        if "2454" in self.Stocks:
            Contract = self.Stocks['2454']
            self.SubscribeContract( Contract )
            Contract.Print()        
        pass
    def OnOrderBook(self, Exchange, Symbol, MsgTime, Msg):
        #implement OnOrderBook() ...
        print('-------------- OnOrderBook() --------------')
        print('--- Exchange[{0}]  Symbol[{1}]  MsgTime[{2}]'.format(Exchange, Symbol, MsgTime))
        print('--- Bid1={0}({1})  Bid2={2}({3})  Bid3={4}({5})  Bid4={6}({7})  Bid5={8}({9})'.format(
            Msg.BidPrice1, Msg.BidQty1, Msg.BidPrice2, Msg.BidQty2, Msg.BidPrice3, Msg.BidQty3, Msg.BidPrice4, Msg.BidQty4, Msg.BidPrice5, Msg.BidQty5))
        print('--- Ask1={0}({1})  Ask2={2}({3})  Ask3={4}({5})  Ask4={6}({7})  Ask5={8}({9})'.format(
            Msg.AskPrice1, Msg.AskQty1, Msg.AskPrice2, Msg.AskQty2, Msg.AskPrice3, Msg.AskQty3, Msg.AskPrice4, Msg.AskQty4, Msg.AskPrice5, Msg.AskQty5))
        print('--- DerivedBid={0}({1})  DerivedAsk={2}({3})'.format(Msg.DerivedBidPrice, Msg.DerivedBidQty, Msg.DerivedAskPrice, Msg.DerivedAskQty))
        print(f'--- IsTestMatch={Msg.IsTestMatch}');
        pass
    def OnTrade(self, Exchange, Symbol, MatchTime, MatchPrice, MatchQty, IsTestMatch):
        #implement OnTrade() ...
        print('-------------- OnTrade() --------------')
        print('--- Exchange[{0}]  Symbol[{1}]'.format(Exchange, Symbol))
        print('--- MatchTime={0}  MatchPrice={1}  MatchQty={2}'.format(MatchTime, MatchPrice, MatchQty))
        print(f'--- IsTestMatch={IsTestMatch}');
        pass

In [59]:
logonOK = False
ObjQuote = testPyQuoteAPI()

print('IsConnected:', str(ObjQuote.IsConnected()))    
#testPyQuoteAPI.py說明:
#訂閱檔數上限20檔
#ObjQuote.Logon('IP', 34567, '身分證字號(大寫字母)', '電子登入密碼', True )
#取消訂閱商品:ObjQuote.UnsubscribeAll()

if not ObjQuote.Logon(QuoteIP, 34567, UID, LoginPW, True ):
    print(f'登入失敗! {ObjQuote.GetLastErrorMsg()}') 
print('IsConnected:', str(ObjQuote.IsConnected()))

IsConnected: False
-------------- OnConnected() --------------
IsConnected: True
-------------- OnLogonResponse() --------------
--- IsSucceed:True ReplyString:Logon OK!
Total Contract Count [77592] 
-------------- OnContractDownloadComplete() --------------
----- [TWSE][2330] -----
Exchange[TWSE] 
Symbol[2330] 
Market[tse] 
DisplayName[台積電] 
Category[24] 
BullPx[977.0] 
BearPx[801.0] 
RefPx[889.0] 
TradeUnit[1000] 
DayTrade[Yes] 
WarringStock[0] 
IsWarrant[False] 
----- TWSE Stocks -----
----- [TWSE][2454] -----
Exchange[TWSE] 
Symbol[2454] 
Market[tse] 
DisplayName[聯發科] 
Category[24] 
BullPx[1520.0] 
BearPx[1250.0] 
RefPx[1385.0] 
TradeUnit[1000] 
DayTrade[Yes] 
WarringStock[0] 
IsWarrant[False] 
----- TWSE Stocks -----


In [60]:
# 退訂商品
ObjQuote.UnsubscribeAll()